# Word2Vec model

In [1]:
import os
import re
import pandas as pd
import random

import matplotlib.pyplot as plt
import urllib.request
from konlpy.tag import Okt, Mecab

from tqdm import tqdm

## data

In [2]:
saturi_path = os.getenv("HOME") + '/aiffel/'
saturi_data = pd.read_csv(saturi_path + 'saturi_crawling_thesaurus_0227.csv')

In [3]:
saturi_data.head()

dial original                                            meaning reg
0   분쉬       분수                               분수의 방언, 사물을 분별하는 지혜.  jj
1   분시       분수                               분수의 방언, 사물을 분별하는 지혜.  jj
2   분절       분결                          분결의 방언, 분한 마음이 왈칵 일어난 바람.  jj
3   분채       부채   부채의 방언, 손으로 흔들어 바람을 일으키는 물건. 대오리로 살을 하고 종이나 헝...  jj
4  분채질      부채질                       부채질의 방언, 부채를 흔들어 바람을 일으키는 일.  jj

In [4]:
print(len(saturi_data))

78042


### 결측치 확인

In [5]:
print(saturi_data.isnull().sum())

dial        0
original    0
meaning     0
reg         0
dtype: int64


### JJ_data

In [6]:
jj = saturi_data[saturi_data['reg'] == 'jj']

In [7]:
jj.reset_index(drop=True, inplace=True)

In [8]:
jj.head()

dial original                                            meaning reg
0   분쉬       분수                               분수의 방언, 사물을 분별하는 지혜.  jj
1   분시       분수                               분수의 방언, 사물을 분별하는 지혜.  jj
2   분절       분결                          분결의 방언, 분한 마음이 왈칵 일어난 바람.  jj
3   분채       부채   부채의 방언, 손으로 흔들어 바람을 일으키는 물건. 대오리로 살을 하고 종이나 헝...  jj
4  분채질      부채질                       부채질의 방언, 부채를 흔들어 바람을 일으키는 일.  jj

In [9]:
print(len(jj))

14622


In [10]:
jj['word2vec'] = (jj['dial'] + '' + jj['original'] + ' ') * 3

/tmp/ipykernel_9414/259037858.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  jj['word2vec'] = (jj['dial'] + '' + jj['original'] + ' ') * 3


In [11]:
jj.head()

dial original                                            meaning reg  \
0   분쉬       분수                               분수의 방언, 사물을 분별하는 지혜.  jj   
1   분시       분수                               분수의 방언, 사물을 분별하는 지혜.  jj   
2   분절       분결                          분결의 방언, 분한 마음이 왈칵 일어난 바람.  jj   
3   분채       부채   부채의 방언, 손으로 흔들어 바람을 일으키는 물건. 대오리로 살을 하고 종이나 헝...  jj   
4  분채질      부채질                       부채질의 방언, 부채를 흔들어 바람을 일으키는 일.  jj   

                   word2vec  
0        분쉬 분수 분쉬 분수 분쉬 분수   
1        분시 분수 분시 분수 분시 분수   
2        분절 분결 분절 분결 분절 분결   
3        분채 부채 분채 부채 분채 부채   
4  분채질 부채질 분채질 부채질 분채질 부채질

### KW_data

In [12]:
kw = saturi_data[saturi_data['reg'] == 'kw']

In [13]:
kw.reset_index(drop=True, inplace=True)

In [14]:
kw.head()

dial original                                            meaning reg
0    분멩       분명                                 분명의 방언, 틀림없이 확실하게.  kw
1    분벨       분별                     분별의 방언, 서로 다른 일이나 사물을 구별하여 가름.  kw
2    분사       분수                               분수의 방언, 사물을 분별하는 지혜.  kw
3  분사머리       분수                               분수의 방언, 사물을 분별하는 지혜.  kw
4    분초       부추   부추의 방언, 백합과의 여러해살이풀. 봄에 땅속의 작은 비늘줄기로부터 길이 30c...  kw

In [15]:
print(len(kw))

14805


### GS_data

In [16]:
gs = saturi_data[saturi_data['reg'] == 'gs']

In [17]:
gs.reset_index(drop=True, inplace=True)

In [18]:
gs.head()

dial original                               meaning reg
0    분래하다     분란하다                분란하다의 방언, 어수선하고 소란스럽다.  gs
1    분산하다     부산하다   부산하다의 방언, 급하게 서두르거나 시끄럽게 떠들어 어수선하다.  gs
2   불구룸하다    불그름하다                     불그름하다의 방언, 조금 붉다.  gs
3   불구리하다    불그레하다                 불그레하다의 방언, 엷게 불그스름하다.  gs
4  불구무리하다   볼그무레하다             볼그무레하다의 방언, 아주 엷게 볼그스름하다.  gs

In [19]:
print(len(gs))

25106


### CC_data

In [20]:
cc = saturi_data[saturi_data['reg'] == 'cc']

In [21]:
cc.reset_index(drop=True, inplace=True)

In [22]:
cc.head()

dial original                                            meaning reg
0   분우기      분위기                           분위기의 방언, 지구를 둘러싸고 있는 기체.  cc
1   불막대     부지깽이   부지깽이의 방언, 아궁이 따위에 불을 땔 때에, 불을 헤치거나 끌어내거나 거두어 ...  cc
2  불막대기     부지깽이   부지깽이의 방언, 아궁이 따위에 불을 땔 때에, 불을 헤치거나 끌어내거나 거두어 ...  cc
3  불쇠바닥       불혀                불혀의 방언, 날름거리며 타오르는 불길을 비유적으로 이르는 말.  cc
4   불여수      불여우       불여우의 방언, 몹시 변덕스럽고 못된, 꾀가 많은 여자를 비유적으로 이르는 말.  cc

In [23]:
print(len(cc))

5856


### JD_data

In [24]:
jd = saturi_data[saturi_data['reg'] == 'jd']

In [25]:
jd.reset_index(drop=True, inplace=True)

In [26]:
jd.head()

dial original                                            meaning reg
0   분대질      분탕질                       분탕질의 방언, 집안의 재물을 다 없애 버리는 짓.  jd
1    분투       부티   부티의 방언, 베를 짤 때, 베틀의 말코 두 끝에 끈을 매어 허리에 두르는 넓은 ...  jd
2    분튀       부티   부티의 방언, 베를 짤 때, 베틀의 말코 두 끝에 끈을 매어 허리에 두르는 넓은 ...  jd
3   붇두둥      불두덩                   불두덩의 방언, 남녀의 생식기 언저리에 있는 불룩한 부분.  jd
4  불강생이     불강아지                            불강아지의 방언, 몸이 바싹 여윈 강아지.  jd

In [27]:
print(len(jd))

17653


## Word2Vec_jj

In [28]:
test = list(jj['word2vec'].values)

In [29]:
tset = []
for i in test:
    i = i.split()
    tset.append(i)

In [30]:
tset

[['분쉬', '분수', '분쉬', '분수', '분쉬', '분수'],
 ['분시', '분수', '분시', '분수', '분시', '분수'],
 ['분절', '분결', '분절', '분결', '분절', '분결'],
 ['분채', '부채', '분채', '부채', '분채', '부채'],
 ['분채질', '부채질', '분채질', '부채질', '분채질', '부채질'],
 ['사둔칩', '사돈집', '사둔칩', '사돈집', '사둔칩', '사돈집'],
 ['분짐', '분김', '분짐', '분김', '분짐', '분김'],
 ['분짓', '분깃', '분짓', '분깃', '분짓', '분깃'],
 ['하르버지', '할아버지', '하르버지', '할아버지', '하르버지', '할아버지'],
 ['불', '벌', '불', '벌', '불', '벌'],
 ['불갈래', '부삽', '불갈래', '부삽', '불갈래', '부삽'],
 ['불갑', '성냥', '불갑', '성냥', '불갑', '성냥'],
 ['불게미', '불똥', '불게미', '불똥', '불게미', '불똥'],
 ['불게예미', '불똥', '불게예미', '불똥', '불게예미', '불똥'],
 ['불곽', '성냥갑', '불곽', '성냥갑', '불곽', '성냥갑'],
 ['불궤수웨', '불쏘시개', '불궤수웨', '불쏘시개', '불궤수웨', '불쏘시개'],
 ['불그네', '고무래', '불그네', '고무래', '불그네', '고무래'],
 ['불근네', '불고무래', '불근네', '불고무래', '불근네', '불고무래'],
 ['불근데', '불고무래', '불근데', '불고무래', '불근데', '불고무래'],
 ['불글레기', '거품', '불글레기', '거품', '불글레기', '거품'],
 ['불깍', '성냥', '불깍', '성냥', '불깍', '성냥'],
 ['불깍지', '등잔', '불깍지', '등잔', '불깍지', '등잔'],
 ['불껑', '재', '불껑', '재', '불껑', '재'],
 ['불끌럭지', '불꾸러미', '불끌럭지', '불

In [31]:
from gensim.models import Word2Vec

model_jj = Word2Vec(sentences = tset, vector_size = 100, window = 3, min_count = 3, workers = 4, sg = 1, epochs = 100)
# sg값 1일 경우 skip-gram, 0일 경우 CBOW
# skip-gram : 해당 단어를 통해 주변단어를 예측
# CBOW : 주변 단어를 통해 해당 단어를 예측

In [32]:
model_jj.wv.similarity('부채', '분채')

0.99645764

In [33]:
print(model_jj.wv.most_similar("시름없다"))

[('시름엇다', 0.9964210987091064), ('시름읏다', 0.996354877948761), ('시름읎다', 0.9959554076194763), ('행실머리', 0.6141220927238464), ('물퀴신', 0.5997700691223145), ('헨실머리', 0.5978392362594604), ('물쿠신', 0.5977985262870789), ('물귀신', 0.5854921340942383), ('어느제', 0.5790910720825195), ('어는제', 0.5770575404167175)]


In [34]:
jj[:50]

dial original                                            meaning reg  \
0     분쉬       분수                               분수의 방언, 사물을 분별하는 지혜.  jj   
1     분시       분수                               분수의 방언, 사물을 분별하는 지혜.  jj   
2     분절       분결                          분결의 방언, 분한 마음이 왈칵 일어난 바람.  jj   
3     분채       부채   부채의 방언, 손으로 흔들어 바람을 일으키는 물건. 대오리로 살을 하고 종이나 헝...  jj   
4    분채질      부채질                       부채질의 방언, 부채를 흔들어 바람을 일으키는 일.  jj   
5    사둔칩      사돈집                              사돈집의 방언, 서로 사돈이 되는 집.  jj   
6     분짐       분김                          분김의 방언, 분한 마음이 왈칵 일어난 바람.  jj   
7     분짓       분깃                     분깃의 방언, 유산을 한 몫 나누어 줌. 또는 그 몫.  jj   
8   하르버지     할아버지                     할아버지의 방언, 부모의 아버지를 이르거나 부르는 말.  jj   
9      불        벌                               벌의 방언, 넓고 평평하게 생긴 땅.  jj   
10   불갈래       부삽   부삽의 방언, 아궁이나 화로의 재를 치거나, 숯불이나 불을 담아 옮기는 데 쓰는 ...  jj   
11    불갑       성냥   성냥의 방언, 마찰에 의하여 불을 일으키는 물건. 작은 나뭇개비의 한쪽 끝에 황 ...  jj   
12   불게미       불똥                    불똥의 방언, 심지의 끝이 다 타서 엉기어 붙은 찌꺼기.  jj   
13  불게예미       불똥                    불똥의 방언, 심지의 끝이 다 타서 엉기어 붙은 찌꺼기.  jj   
14    불곽      성냥갑   성냥갑의 방언, 성냥개비를 넣는 갑. 측면에 유리 가루, 규사, 규조토 따위가 발...  jj   
15  불궤수웨     불쏘시개   불쏘시개의 방언, 불을 때거나 피울 적에 불이 쉽게 옮겨붙게 하기 위하여 먼저 태...  jj   
16   불그네      고무래   고무래의 방언, 곡식을 그러모으고 펴거나, 밭의 흙을 고르거나 아궁이의 재를 긁어...  jj   
17   불근네     불고무래   불고무래의 방언, 아궁이의 불을 밀어 넣거나 한데 모아 당기어 밖으로 내는 데 쓰...  jj   
18   불근데     불고무래   불고무래의 방언, 아궁이의 불을 밀어 넣거나 한데 모아 당기어 밖으로 내는 데 쓰...  jj   
19  불글레기       거품              거품의 방언, 액체가 기체를 머금고 부풀어서 생긴, 속이 빈 방울.  jj   
20    불깍       성냥   성냥의 방언, 마찰에 의하여 불을 일으키는 물건. 작은 나뭇개비의 한쪽 끝에 황 ...  jj   
21   불깍지       등잔                    등잔의 방언, 기름을 담아 등불을 켜는 데에 쓰는 그릇.  jj   
22    불껑        재                         재의 방언, 불에 타고 남는 가루 모양의 물질.  jj   
23  불끌럭지     불꾸러미             불꾸러미의 방언, 불씨를 옮기기 위하여 짚 뭉치 따위에 옮겨붙인 불.  jj   
24  불끌레기     불꾸러미             불꾸러미의 방언, 불씨를 옮기기 위하여 짚 뭉치 따위에 옮겨붙인 불.  jj   
25  불닥새기       불알                           불알의 방언, 고환을 일상적으로 이르는 말.  jj   
26  불닥세기       불알      불알의 방언 제주 지역에서는 불세기로도 적는다., 고환을 일상적으로 이르는 말.  jj   
27    불도       산신                             산신의 방언, 산을 지키고 다스리는 신.  jj   
28   불땡이     부지깽이   부지깽이의 방언, 아궁이 따위에 불을 땔 때에, 불을 헤치거나 끌어내거나 거두어 ...  jj   
29   불란지     개똥벌레   개똥벌레의 방언, 반딧불잇과의 딱정벌레. 몸의 길이는 1.2~1.8cm이며, 검은...  jj   
30   불미질      대장일           대장일의 방언, 수공업적인 방법으로 쇠를 달구어 연장 따위를 만드는 일.  jj   
31   불망골       불똥                    불똥의 방언, 심지의 끝이 다 타서 엉기어 붙은 찌꺼기.  jj   
32  불망구리       불똥                    불똥의 방언, 심지의 끝이 다 타서 엉기어 붙은 찌꺼기.  jj   
33  불망텡이     불알망태                           불알망태의 방언, 음낭을 속되게 이르는 말.  jj   
34  불매대장     대장장이         대장장이의 방언, 쇠를 달구어 연장 따위를 만드는 일을 직업으로 하는 사람.  jj   
35   불매질      대장일           대장일의 방언, 수공업적인 방법으로 쇠를 달구어 연장 따위를 만드는 일.  jj   
36    불미       풀무   풀무의 방언, 불을 피울 때에 바람을 일으키는 기구. 골풀무와 손풀무 두 가지가 있다.  jj   
37   불미간      대장간                      대장간의 방언, 쇠를 달구어 온갖 연장을 만드는 곳.  jj   
38   하르비     할아버지                     할아버지의 방언, 부모의 아버지를 이르거나 부르는 말.  jj   
39  불미대장     대장장이         대장장이의 방언, 쇠를 달구어 연장 따위를 만드는 일을 직업으로 하는 사람.  jj   
40  불미와찌     대장장이         대장장이의 방언, 쇠를 달구어 연장 따위를 만드는 일을 직업으로 하는 사람.  jj   
41   불미왕      대장간                      대장간의 방언, 쇠를 달구어 온갖 연장을 만드는 곳.  jj   
42  불미쟁이     대장장이         대장장이의 방언, 쇠를 달구어 연장 따위를 만드는 일을 직업으로 하는 사람.  jj   
43   불미칩      대장간                      대장간의 방언, 쇠를 달구어 온갖 연장을 만드는 곳.  jj   
44   불밋간      대장간                      대장간의 방언, 쇠를 달구어 온갖 연장을 만드는 곳.  jj   
45  불방둥이      불장난                             불장난의 방언, 불을 가지고 노는 장난.  jj   
46    불벳       불볕                            불볕의 방언, 몹시 뜨겁게 내리쬐는 햇볕.  jj   
47    불벹       불볕                            불볕의 방언, 몹시 뜨겁게 내리쬐는 햇볕.  jj   
48    불삽       부삽   부삽의 방언, 아궁이나 화로의 재를 치거나, 숯불이나 불을 담아 옮기는 데 쓰는 ...  jj   
49  불소슬게     불쏘시개   불쏘시개의 방언, 불을 때거나 피울 적에 불이 쉽게 옮겨붙게 하기 위하여 먼저 태...  jj   

                          word2vec  
0               분쉬 분수 분쉬 분수 분쉬 분수   
1               분시 분수 분시 분수 분시 분수   
2               

In [35]:
model_jj.wv.vectors.shape

(21152, 100)

## Data Augmentation

### Lexical Substitution 구현하기(표준어 -> 사투리)

In [39]:
def lexical_sub(sentence, word2vec):
    res = ""
    sentence = sentence.values
    tt = []
    for i in sentence:
        i = i.split()
        tt.append(i)

    try:
        _from = random.choice(tt)
        _to = word2vec.wv.most_similar(_from)[0][0]
        
    except:   # 단어장에 없는 단어
        return None

    for tok in tt:
        if tok is _from:
            res += _to + " "
        else:
            res += str(tok) + " "

    return res

In [40]:
new_corpus = []

for old_src in tqdm(jj['original'].values):
    new_src = lexical_sub(jj['original'], model_jj)
    if new_src is not None: 
        new_corpus.append(new_src)
    # Augmentation이 없더라도 원본 문장을 포함시킵니다
    new_corpus.append(old_src)

print(new_corpus[:50])

100%|██████████| 14622/14622 [13:53<00:00, 17.54it/s]

["['분수'] ['분수'] ['분결'] ['부채'] ['부채질'] ['사돈집'] ['분김'] ['분깃'] ['할아버지'] ['벌'] ['부삽'] ['성냥'] ['불똥'] ['불똥'] ['성냥갑'] ['불쏘시개'] ['고무래'] ['불고무래'] ['불고무래'] ['거품'] ['성냥'] ['등잔'] ['재'] ['불꾸러미'] ['불꾸러미'] ['불알'] ['불알'] ['산신'] ['부지깽이'] ['개똥벌레'] ['대장일'] ['불똥'] ['불똥'] ['불알망태'] ['대장장이'] ['대장일'] ['풀무'] ['대장간'] ['할아버지'] ['대장장이'] ['대장장이'] ['대장간'] ['대장장이'] ['대장간'] ['대장간'] ['불장난'] ['불볕'] ['불볕'] ['부삽'] ['불쏘시개'] ['불쏘시개'] ['불쏘시개'] ['부손'] ['부순'] ['부손'] ['불쏘시개'] ['불쏘시개'] ['불알망태'] ['아궁이'] ['부지깽이'] ['불잉걸'] ['불잉걸'] ['부젓가락'] ['부젓가락'] ['등잔'] ['부젓가락'] ['불김'] ['부젓가락'] ['부싯깃'] ['불똥'] ['불알망태'] ['불알망태'] ['산마루'] ['땅꽈리'] ['불똥'] ['개똥벌레'] ['반딧불이'] ['개똥벌레'] ['불화로'] ['반딧불이'] ['뿌리'] ['붉가시나무'] ['붉가시나무'] ['불개미'] ['게걸쟁이'] ['노른자'] ['아침놀'] ['저녁노을'] ['붓두껍'] ['붓두껍'] ['불알'] ['거적눈'] ['솜바지'] ['붕장어'] ['뱀장어'] ['부채'] ['삐침'] ['북'] ['빚꾸러기'] ['두툽상어'] ['복상어'] ['수염상어'] ['두툽상어'] ['두툽상어'] ['비탈'] ['부끄럼'] ['비녀'] ['비름'] ['비름'] ['비름'] ['북바늘'] ['수수'] ['수수'] ['비듬'] ['비듬'] ['비둘기'] ['빗접'] ['비탈길'] ['비린내'] ['조금'] ['비료'] ['벨벳'] ['옴'] ['옴쟁이'] ['딴총박이'] ['처녀'] ['